## Configuração Inicial

### Importação das Bibliotecas

In [87]:
import pandas as pd
import networkx as nx
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
import scipy
import plotly.graph_objects as go
import leidenalg as la
import igraph as ig
from sklearn.metrics import normalized_mutual_info_score, adjusted_rand_score
from cdlib import evaluation

### Carregamento do Dataset

In [88]:
# Load the dataset
votacao_parlamentar = pd.read_csv('../data/votacao_parlamentar.csv')
print("votacao_parlamentar loaded")

proposicao_tema = pd.read_csv('../data/proposicao_tema.csv')
print("proposicao_tema loaded")

orgao_deputado = pd.read_csv('../data/orgao_deputado.csv')
print("orgao_deputado loaded")

proposicao_microdados = pd.read_csv('../data/proposicao_microdados.csv')
print("proposicao_microdados loaded")

votacao = pd.read_csv('../data/votacao.csv')
print("votacao loaded")

votacao_objeto = pd.read_csv('../data/votacao_objeto.csv')
print("votacao_objeto loaded")

votacao_parlamentar loaded
proposicao_tema loaded
orgao_deputado loaded


e:\Anaconda\envs\camara-analysis_2\lib\site-packages\IPython\core\interactiveshell.py:3577: DtypeWarning:

Columns (13) have mixed types.Specify dtype option on import or set low_memory=False.



proposicao_microdados loaded
votacao loaded
votacao_objeto loaded


### Visualização dos Datasets

In [89]:
proposicao_tema

ano  id_proposicao tipo_proposicao  numero          tema  \
0       1949.0         189908              PL  1270.0         Saúde   
1       1949.0         191295              PL  1374.0         Saúde   
2       1949.0         190123              PL  1286.0         Saúde   
3       1949.0         191012              PL  1353.0         Saúde   
4       1949.0         169918              PL     1.0         Saúde   
...        ...            ...             ...     ...           ...   
256914  2007.0         339917             TVR  1324.0  Comunicações   
256915  2007.0         339920             TVR  1327.0  Comunicações   
256916  2007.0         346704             TVR    74.0  Comunicações   
256917  2007.0         347577             TVR   100.0  Comunicações   
256918  2007.0         349140             TVR   116.0  Comunicações   

        relevancia  
0                0  
1                0  
2                0  
3                0  
4                0  
...            ...  
256914           0  
256915           0  
256916           0  
256917           0  
256918           0  

[256919 rows x 6 columns]

In [90]:
votacao_parlamentar

id_votacao        data   horario voto  id_deputado  \
0           1454169  2002-02-26  20:39:33  Sim      74673.0   
1           2130649  2002-12-18  13:20:09  Sim      74673.0   
2          32428111  2002-03-19  20:39:29  Sim      74680.0   
3           9881418  2002-12-11  23:42:16  Sim      73793.0   
4           1466544  2002-04-23  19:30:24  Sim      73795.0   
...             ...         ...       ...  ...          ...   
1582550    23872668  2023-09-13  18:09:15  Não     204526.0   
1582551   240907634  2023-12-13  20:46:25  Não     204526.0   
1582552   240006823  2023-12-19  20:50:11  Sim     204526.0   
1582553  2125189174  2023-11-29  19:59:38  Não     204526.0   
1582554   240006820  2023-12-19  20:29:15  Sim     204526.0   

                                        nome sigla_partido sigla_uf  \
0                                  Max Mauro           PTB       ES   
1                                  Max Mauro           PTB       ES   
2                                 Dr. Heleno          PSDB       RJ   
3                                 Edinho Bez          PMDB       SC   
4                                 Hugo Biehl           PPB       SC   
...                                      ...           ...      ...   
1582550  Luiz Philippe de Orleans e Bragança            PL       SP   
1582551  Luiz Philippe de Orleans e Bragança            PL       SP   
1582552  Luiz Philippe de Orleans e Bragança            PL       SP   
1582553  Luiz Philippe de Orleans e Bragança            PL       SP   
1582554  Luiz Philippe de Orleans e Bragança            PL       SP   

         id_legislatura  
0                    51  
1                    51  
2                    51  
3                    51  
4                    51  
...                 ...  
1582550              57  
1582551              57  
1582552              57  
1582553              57  
1582554              57  

[1582555 rows x 9 columns]

In [91]:
orgao_deputado

id_orgao                                               nome     sigla  \
0             4              Mesa Diretora da Câmara dos Deputados      MESA   
1             4              Mesa Diretora da Câmara dos Deputados      MESA   
2             4              Mesa Diretora da Câmara dos Deputados      MESA   
3             4              Mesa Diretora da Câmara dos Deputados      MESA   
4             4              Mesa Diretora da Câmara dos Deputados      MESA   
...         ...                                                ...       ...   
85180      5304  Comissão Parlamentar de Inquérito destinada a ...  CPIALIME   
85181      5304  Comissão Parlamentar de Inquérito destinada a ...  CPIALIME   
85182      5304  Comissão Parlamentar de Inquérito destinada a ...  CPIALIME   
85183      5304  Comissão Parlamentar de Inquérito destinada a ...  CPIALIME   
85184      5338  Comissão Especial destinada a apreciar e  prof...  PEC63999   

            nome_deputado                      cargo sigla_uf data_inicio  \
0              Marco Maia         1º Vice-Presidente      NaN  2009-02-02   
1      Inocêncio Oliveira              3º Secretário      NaN  2011-02-01   
2             Aécio Neves                 Presidente       MG  2001-02-14   
3                  Paulão  4º Suplente de Secretário       AL  2020-07-08   
4           Eduardo Gomes              1º Secretário      NaN  2011-02-01   
...                   ...                        ...      ...         ...   
85180    Celcita Pinheiro                 Presidente      NaN  1999-06-08   
85181       Elton Rohnelt                   Suplente      NaN  1999-05-20   
85182  Philemon Rodrigues                   Suplente      NaN  1999-05-20   
85183  Francistônio Pinto                    Titular      NaN  1999-05-20   
85184       Elton Rohnelt                   Suplente      NaN  1999-10-06   

       data_final sigla_partido  
0      2010-12-16           NaN  
1      2013-02-04           NaN  
2      2002-12-17          PSDB  
3      2021-02-01            PT  
4      2013-02-04           NaN  
...           ...           ...  
85180  2000-02-15           NaN  
85181  2000-02-15           NaN  
85182  2000-02-15           NaN  
85183  2000-02-15           NaN  
85184  2000-02-15           NaN  

[85185 rows x 9 columns]

In [92]:
proposicao_microdados

ano        data   horario  id_proposicao  \
0       1961  1961-03-07  00:00:00         159771   
1       1961  1961-03-02  00:00:00         162927   
2       1961  1961-08-29  00:00:00         164227   
3       1961  1961-03-09  00:00:00         162978   
4       1961  1961-09-07  00:00:00         163136   
...      ...         ...       ...            ...   
773683  2023  2023-06-20  19:52:54        2370652   
773684  2023  2023-06-28  19:38:37        2371844   
773685  2023  2023-05-11  11:37:02        2361829   
773686  2023  2023-10-24  13:28:04        2398392   
773687  2023  2023-08-01  20:01:00        2374964   

                                                      url  numero sigla  \
0       https://dadosabertos.camara.leg.br/api/v2/prop...       6   INC   
1       https://dadosabertos.camara.leg.br/api/v2/prop...      95   MSC   
2       https://dadosabertos.camara.leg.br/api/v2/prop...     471   MSC   
3       https://dadosabertos.camara.leg.br/api/v2/prop...     108   MSC   
4       https://dadosabertos.camara.leg.br/api/v2/prop...     150   MSC   
...                                                   ...     ...   ...   
773683  https://dadosabertos.camara.leg.br/api/v2/prop...      15   REC   
773684  https://dadosabertos.camara.leg.br/api/v2/prop...      17   REC   
773685  https://dadosabertos.camara.leg.br/api/v2/prop...       6   REC   
773686  https://dadosabertos.camara.leg.br/api/v2/prop...      32   REC   
773687  https://dadosabertos.camara.leg.br/api/v2/prop...      18   REC   

                                                     tipo  \
0                                               Indicação   
1                                                Mensagem   
2                                                Mensagem   
3                                                Mensagem   
4                                                Mensagem   
...                                                   ...   
773683  Recurso contra decisão de Presidente de Comiss...   
773684  Recurso contra decisão de Presidente de Comiss...   
773685  Recurso contra decisão de Presidente de Comiss...   
773686  Recurso contra decisão de Presidente de Comiss...   
773687  Recurso contra decisão de Presidente de Comiss...   

                                                   ementa ementa_detalhada  \
0       SUGERE AUDIENCIA DA COMISSÃO DE CONSTITUIÇÃO E...              NaN   
1       SOLICITANDO SEJA SOBRESTADO O ANDAMENTO DO PRO...              NaN   
2       SUBMETE A CONSIDERAÇÃO DO CONGRESSO NACIONAL O...              NaN   
3       ENCAMINHA TEXTO DA 'DECLARAÇÃO SOBRE A ADESÃO ...              NaN   
4       SUBMETE A APRECIAÇÃO DO CONGRESSO NACIONAL A '...              NaN   
...                                                   ...              ...   
773683  O presente recurso tem como fundamento de apre...              NaN   
773684  O presente recurso tem como fundamento de apre...              NaN   
773685  Recurso contra a Decisão da Presidência da CFF...              NaN   
773686  Recorre da decisão proferida pela Presidência ...              NaN   
773687  RECURSO A QUESTÃO DE ORDEM APRESENTADA NA CPI ...              NaN   

        ... data_hora_ultimo_status url_relator_ultimo_status  \
0       ...     1961-03-07T00:00:00                       NaN   
1       ...     1961-03-02T00:00:00                       NaN   
2       ...     1961-08-29T00:00:00                       NaN   
3       ...     1961-03-09T00:00:00                       NaN   
4       ...     1963-06-12T00:00:00                       NaN   
...     ...                     ...                       ...   
773683  ...     2023-06-20T19:52:54                       NaN   
773684  ...     2023-06-28T19:38:37                       NaN   
773685  ...     2023-05-11T11:37:02                       NaN   
773686  ...     2023-10-24T13:28:04                       NaN   
773687  ...     2023-08-09T00:00:00                       NaN   

       sigla_orgao_u

In [93]:
votacao

id_votacao        data data_registro horario_registro  id_orgao  \
0         21681112  1997-07-10    2009-07-10         16:35:17         4   
1           217554  1997-07-10    2009-07-10         16:35:22         4   
2          2181414  2001-12-13           NaN              NaN         4   
3          4157714  2003-01-29           NaN              NaN         4   
4         33985042  2007-03-12    2007-03-19         11:29:06         4   
...            ...         ...           ...              ...       ...   
162356    24119512  2023-12-12    2023-12-12         15:56:28    539635   
162357    24119152  2023-12-12    2023-12-12         15:56:27    539635   
162358    24119562  2023-12-12    2023-12-12         15:56:28    539635   
162359    24119542  2023-12-12    2023-12-12         15:56:28    539635   
162360    24090183  2023-12-05    2023-12-05         15:11:18    539638   

       sigla_orgao  id_evento  aprovacao  voto_sim  voto_nao  voto_outro  \
0             MESA          0        1.0         0         0           0   
1             MESA          0        1.0         0         0           0   
2             MESA          0        1.0         0         0           0   
3             MESA          0        1.0         0         0           0   
4             MESA          0        1.0         0         0           0   
...            ...        ...        ...       ...       ...         ...   
162356    CEDESNAT      71530        1.0         0         0           0   
162357    CEDESNAT      71530        1.0         0         0           0   
162358    CEDESNAT      71530        1.0         0         0           0   
162359    CEDESNAT      71530        1.0         0         0           0   
162360    PEC00523      71408        1.0         0         0           0   

                                                descricao  \
0                                                     NaN   
1                                                     NaN   
2       Matéria sobre a mesa (REQUERIMENTO DE URGÊNCIA...   
3       Aprovação unânime do parecer da Relatora, Dep....   
4       Deferido o requerimento REQ 487/2007 => MPV 35...   
...                                                   ...   
162356                                          Aprovado.   
162357                                          Aprovado.   
162358                                          Aprovado.   
162359                                          Aprovado.   
162360                                          Aprovado.   

       data_hora_ultima_votacao descricao_ultima_votacao  \
0                           NaN                      NaN   
1                           NaN                      NaN   
2                           NaN                      NaN   
3                           NaN                      NaN   
4                           NaN                      NaN   
...                         ...                      ...   
162356                      NaN                      NaN   
162357                      NaN                      NaN   
162358                      NaN                      NaN   
162359                      NaN                      NaN   
162360                      NaN                      NaN   

       data_hora_ultima_proposicao  id_ultima_proposicao  \
0                              NaN                     0   
1                              NaN                     0   
2                              NaN                     0   
3                              NaN                     0   
4                              NaN                     0   
...                            ...                   ...   
162356                         NaN                     0   
162357                         NaN                     0   
162358                         NaN                     0   
162359                         NaN                     0   
162360                         NaN                     0   

                   

In [94]:
votacao_objeto

id_votacao        data  \
0          2102743  1994-06-21   
1          2102742  1994-06-21   
2          2102742  1994-06-21   
3          2102742  1994-06-21   
4          2102743  1994-06-21   
...            ...         ...   
628223    19156529  1968-09-23   
628224    19575813  1968-11-29   
628225    19575817  1968-12-05   
628226     1957587  1968-10-22   
628227     2182776  1968-09-18   

                                                descricao  id_proposicao  \
0       0    REJEITADO O PARECER DO RRELATOR, DEP. LUI...         305275   
1       0    REJEITADO O PARECER DO RRELATOR, DEP. LUI...         305275   
2       0    REJEITADO O PARECER DO RRELATOR, DEP. LUI...         305276   
3       0    REJEITADO O PARECER DO RRELATOR, DEP. LUI...          23511   
4       0    REJEITADO O PARECER DO RRELATOR, DEP. LUI...          23511   
...                                                   ...            ...   
628223  0     APROVAÇÃO UNÂNIME DA REDAÇÃO FINAL (PL 1...         191565   
628224  0     APROVAÇÃO UNÂNIME DA REDAÇÃO FINAL (PL 1...         195758   
628225  0     APROVAÇÃO UNÂNIME DA REDAÇÃO FINAL (PL 1...         195758   
628226  0     APROVAÇÃO UNÂNIME DA REDAÇÃO FINAL (PL 1...         195758   
628227  0     APROVAÇÃO UNÂNIME DA REDAÇÃO FINAL (PL 1...         218277   

        ano_proposicao                                             ementa  \
0                  NaN  0    CONTRA INDEFERIMENTO DE REQUERIMENTO DE I...   
1                  NaN  0    CONTRA INDEFERIMENTO DE REQUERIMENTO DE I...   
2                  NaN  0    CONTRA INDEFERIMENTO DE REQUERIMENTO DE I...   
3               1994.0  0    CONTRA INDEFERIMENTO DE REQUERIMENTO DE I...   
4               1994.0  0    CONTRA INDEFERIMENTO DE REQUERIMENTO DE I...   
...                ...                                                ...   
628223          1968.0  0     AUTORIZA O TESOURO NACIONAL A PROMOVER A...   
628224          1968.0  0     AUTORIZA O TESOURO NACIONAL A PROMOVER A...   
628225          1968.0  0     AUTORIZA O TESOURO NACIONAL A PROMOVER A...   
628226          1968.0  0     AUTORIZA O TESOURO NACIONAL A PROMOVER A...   
628227          1966.0  0     AUTORIZA O TESOURO NACIONAL A PROMOVER A...   

        codigo_tipo sigla_tipo  numero                         titulo  
0               192        PPP     1.0      PPP 1 CFT => PL 4650/1994  
1               192        PPP     1.0      PPP 1 CFT => PL 4650/1994  
2               192        PPP     1.0     PPP 1 CCJC => PL 4650/1994  
3               132        EMS  4650.0  EMS 4650/1994 => PL 4650/1994  
4               132        EMS  4650.0  EMS 4650/1994 => PL 4650/1994  
...             ...        ...     ...                            ...  
628223          139         PL  1394.0                   PL 1394/1968  
628224          139         PL  1750.0                   PL 1750/1968  
628225          139         PL  1750.0                   PL 1750/1968  
628226          139         PL  1750.0                   PL 1750/1968  
628227          139         PL  4045.0                   PL 4045/1966  

[628228 rows x 10 columns]

### Seleção, tratamento e filtragem dos Dados

In [95]:
Year = 2023

In [96]:
# Selecionar colunas relevantes das tabelas
votacao_objeto['data'] = pd.to_datetime(votacao_objeto['data'])
votacao_objeto = votacao_objeto[votacao_objeto['data'].dt.year == Year]
votacao_objeto = votacao_objeto[['id_votacao', 'id_proposicao', 'data', 'sigla_tipo']]

proposicao_tema = proposicao_tema[proposicao_tema['ano'] == Year]
proposicao_tema = proposicao_tema[['id_proposicao', 'tema', 'relevancia']]

votacao_parlamentar['data'] = pd.to_datetime(votacao_parlamentar['data'])
votacao_parlamentar = votacao_parlamentar[votacao_parlamentar['data'].dt.year == Year]
votacao_parlamentar = votacao_parlamentar[['id_votacao', 'id_deputado', 'voto', 'nome', 'sigla_partido', 'sigla_uf']]

votacao['data'] = pd.to_datetime(votacao['data'])
votacao = votacao[votacao['data'].dt.year == Year]
votacao = votacao[['id_votacao', 'id_orgao', 'sigla_orgao', 'aprovacao']]

orgao_deputado = orgao_deputado.drop_duplicates(subset='id_orgao')
orgao_deputado = orgao_deputado[['id_orgao', 'nome']]
orgao_deputado = orgao_deputado.rename(columns={'nome': 'nome_orgao'})

proposicao_microdados['data'] = pd.to_datetime(proposicao_microdados['data'])
proposicao_microdados = proposicao_microdados[proposicao_microdados['data'].dt.year == Year]
proposicao_microdados = proposicao_microdados[['id_proposicao', 'tipo']]

In [97]:
merged_df = pd.merge(votacao_objeto, proposicao_tema, on='id_proposicao', how='left')
merged_df = pd.merge(merged_df, proposicao_microdados, on='id_proposicao', how='left')
merged_df = pd.merge(merged_df, votacao_parlamentar, on='id_votacao', how='left')
merged_df = pd.merge(merged_df, votacao, on='id_votacao', how='left')
merged_df = pd.merge(merged_df, orgao_deputado, on='id_orgao', how='left')

# Convert the "data" column to datetime
merged_df['data'] = pd.to_datetime(merged_df['data'])
print("Converted 'data' column to datetime")

# Extract the year from the "data" column
merged_df['year'] = merged_df['data'].dt.year
print("Extracted year from 'data' column")

merged_df = merged_df.dropna(subset=['voto'])

merged_df

Converted 'data' column to datetime
Extracted year from 'data' column


id_votacao  id_proposicao       data sigla_tipo  \
17        234536850        2354474 2023-03-30        PLV   
18        234536850        2354474 2023-03-30        PLV   
19        234536850        2354474 2023-03-30        PLV   
20        234536850        2354474 2023-03-30        PLV   
21        234536850        2354474 2023-03-30        PLV   
...             ...            ...        ...        ...   
5967580   227727964        2396324 2023-10-17        RPD   
5967581   227727964        2396324 2023-10-17        RPD   
5967582   227727964        2396324 2023-10-17        RPD   
5967583   227727964        2396324 2023-10-17        RPD   
5967584   227727964        2396324 2023-10-17        RPD   

                                                tema  relevancia  \
17       Agricultura, Pecuária, Pesca e Extrativismo         0.0   
18       Agricultura, Pecuária, Pesca e Extrativismo         0.0   
19       Agricultura, Pecuária, Pesca e Extrativismo         0.0   
20       Agricultura, Pecuária, Pesca e Extrativismo         0.0   
21       Agricultura, Pecuária, Pesca e Extrativismo         0.0   
...                                              ...         ...   
5967580                                          NaN         NaN   
5967581                                          NaN         NaN   
5967582                                          NaN         NaN   
5967583                                          NaN         NaN   
5967584                                          NaN         NaN   

                                                  tipo  id_deputado voto  \
17                         Projeto de Lei de Conversão     204364.0  Sim   
18                         Projeto de Lei de Conversão     220558.0  Sim   
19                         Projeto de Lei de Conversão     220587.0  Não   
20                         Projeto de Lei de Conversão     178964.0  Não   
21                         Projeto de Lei de Conversão     178987.0  Não   
...                                                ...          ...  ...   
5967580  Requerimento de Votação pelo Processo Nominal     220588.0  Não   
5967581  Requerimento de Votação pelo Processo Nominal     165470.0  Não   
5967582  Requerimento de Votação pelo Processo Nominal      91228.0  Não   
5967583  Requerimento de Votação pelo Processo Nominal     178873.0  Não   
5967584  Requerimento de Votação pelo Processo Nominal     220639.0  Não   

                      nome sigla_partido sigla_uf  id_orgao sigla_orgao  \
17              Eli Borges            PL       TO       180        PLEN   
18               Zé Trovão            PL       SC       180        PLEN   
19            Gerlen Diniz            PP       AC       180        PLEN   
20           Heitor Schuch           PSB       RS       180        PLEN   
21           Orlando Silva         PCdoB       SP       180        PLEN   
...                    ...           ...      ...       ...         ...   
5967580     Roberto Duarte  REPUBLICANOS       AC      2003        CCJC   
5967581  Rodrigo Valadares         UNIÃO       SE      2003        CCJC   
5967582  Waldemar Oliveira        AVANTE       PE      2003        CCJC   
5967583     Helder Salomão            PT       ES      2003        CCJC   
5967584   Guilherme Boulos          PSOL       SP      2003        CCJC   

         aprovacao                                         nome_orgao  year  
17             1.0                                           Plenário  2023  
18             1.0                                           Plenário  2023  
19             1.0                                           Plenário  2023  
20             1.0                                           Plenário  2023  
21             1.0                                           Plenário  2023  
...            ...                                                ...   ...  
5967580        0.0  Comissão de Constituição e Justiça e de Cidadania  2023  
5967581        0.0  Comissão de C

In [98]:
# Count the number of votes for each proposition
votes_per_proposition = merged_df['id_votacao'].value_counts()
print("Counted number of votes for each proposition")
print(votes_per_proposition.head())

# Filter propositions with more than 200 votes
propositions_with_more_than_200_votes = votes_per_proposition[votes_per_proposition > 200].index
print(f"Filtered propositions with more than 200 votes: {len(propositions_with_more_than_200_votes)} propositions")

# Filter the dataset to include only these propositions
votacao_ano = merged_df[merged_df['id_votacao'].isin(propositions_with_more_than_200_votes)]
print(f"Filtered dataset to include only propositions with more than 200 votes: {len(votacao_ano)} rows")

Counted number of votes for each proposition
2357053110    74315
2357053108    74148
2357053105    74148
2357053119    73981
2357053122    70975
Name: id_votacao, dtype: int64
Filtered propositions with more than 200 votes: 384 propositions
Filtered dataset to include only propositions with more than 200 votes: 5925852 rows


In [99]:
votacao_ano

id_votacao  id_proposicao       data sigla_tipo  \
17        234536850        2354474 2023-03-30        PLV   
18        234536850        2354474 2023-03-30        PLV   
19        234536850        2354474 2023-03-30        PLV   
20        234536850        2354474 2023-03-30        PLV   
21        234536850        2354474 2023-03-30        PLV   
...             ...            ...        ...        ...   
5967580   227727964        2396324 2023-10-17        RPD   
5967581   227727964        2396324 2023-10-17        RPD   
5967582   227727964        2396324 2023-10-17        RPD   
5967583   227727964        2396324 2023-10-17        RPD   
5967584   227727964        2396324 2023-10-17        RPD   

                                                tema  relevancia  \
17       Agricultura, Pecuária, Pesca e Extrativismo         0.0   
18       Agricultura, Pecuária, Pesca e Extrativismo         0.0   
19       Agricultura, Pecuária, Pesca e Extrativismo         0.0   
20       Agricultura, Pecuária, Pesca e Extrativismo         0.0   
21       Agricultura, Pecuária, Pesca e Extrativismo         0.0   
...                                              ...         ...   
5967580                                          NaN         NaN   
5967581                                          NaN         NaN   
5967582                                          NaN         NaN   
5967583                                          NaN         NaN   
5967584                                          NaN         NaN   

                                                  tipo  id_deputado voto  \
17                         Projeto de Lei de Conversão     204364.0  Sim   
18                         Projeto de Lei de Conversão     220558.0  Sim   
19                         Projeto de Lei de Conversão     220587.0  Não   
20                         Projeto de Lei de Conversão     178964.0  Não   
21                         Projeto de Lei de Conversão     178987.0  Não   
...                                                ...          ...  ...   
5967580  Requerimento de Votação pelo Processo Nominal     220588.0  Não   
5967581  Requerimento de Votação pelo Processo Nominal     165470.0  Não   
5967582  Requerimento de Votação pelo Processo Nominal      91228.0  Não   
5967583  Requerimento de Votação pelo Processo Nominal     178873.0  Não   
5967584  Requerimento de Votação pelo Processo Nominal     220639.0  Não   

                      nome sigla_partido sigla_uf  id_orgao sigla_orgao  \
17              Eli Borges            PL       TO       180        PLEN   
18               Zé Trovão            PL       SC       180        PLEN   
19            Gerlen Diniz            PP       AC       180        PLEN   
20           Heitor Schuch           PSB       RS       180        PLEN   
21           Orlando Silva         PCdoB       SP       180        PLEN   
...                    ...           ...      ...       ...         ...   
5967580     Roberto Duarte  REPUBLICANOS       AC      2003        CCJC   
5967581  Rodrigo Valadares         UNIÃO       SE      2003        CCJC   
5967582  Waldemar Oliveira        AVANTE       PE      2003        CCJC   
5967583     Helder Salomão            PT       ES      2003        CCJC   
5967584   Guilherme Boulos          PSOL       SP      2003        CCJC   

         aprovacao                                         nome_orgao  year  
17             1.0                                           Plenário  2023  
18             1.0                                           Plenário  2023  
19             1.0                                           Plenário  2023  
20             1.0                                           Plenário  2023  
21             1.0                                           Plenário  2023  
...            ...                                                ...   ...  
5967580        0.0  Comissão de Constituição e Justiça e de Cidadania  2023  
5967581        0.0  Comissão de C

In [100]:
votacao_plenario = votacao_ano.loc[votacao_ano['nome_orgao'] == 'Plenário']

In [101]:
votacao_plenario

id_votacao  id_proposicao       data sigla_tipo  \
17        234536850        2354474 2023-03-30        PLV   
18        234536850        2354474 2023-03-30        PLV   
19        234536850        2354474 2023-03-30        PLV   
20        234536850        2354474 2023-03-30        PLV   
21        234536850        2354474 2023-03-30        PLV   
...             ...            ...        ...        ...   
5957569  2115253183        2402982 2023-11-08        PSS   
5957570  2115253183        2402982 2023-11-08        PSS   
5957571  2115253183        2402982 2023-11-08        PSS   
5957572  2115253183        2402982 2023-11-08        PSS   
5957573  2115253183        2402982 2023-11-08        PSS   

                                                tema  relevancia  \
17       Agricultura, Pecuária, Pesca e Extrativismo         0.0   
18       Agricultura, Pecuária, Pesca e Extrativismo         0.0   
19       Agricultura, Pecuária, Pesca e Extrativismo         0.0   
20       Agricultura, Pecuária, Pesca e Extrativismo         0.0   
21       Agricultura, Pecuária, Pesca e Extrativismo         0.0   
...                                              ...         ...   
5957569                                          NaN         NaN   
5957570                                          NaN         NaN   
5957571                                          NaN         NaN   
5957572                                          NaN         NaN   
5957573                                          NaN         NaN   

                                                    tipo  id_deputado voto  \
17                           Projeto de Lei de Conversão     204364.0  Sim   
18                           Projeto de Lei de Conversão     220558.0  Sim   
19                           Projeto de Lei de Conversão     220587.0  Não   
20                           Projeto de Lei de Conversão     178964.0  Não   
21                           Projeto de Lei de Conversão     178987.0  Não   
...                                                  ...          ...  ...   
5957569  Parecer às Emendas ou ao Substitutivo do Senado     220526.0  Não   
5957570  Parecer às Emendas ou ao Substitutivo do Senado     204398.0  Sim   
5957571  Parecer às Emendas ou ao Substitutivo do Senado     220621.0  Não   
5957572  Parecer às Emendas ou ao Substitutivo do Senado     178993.0  Sim   
5957573  Parecer às Emendas ou ao Substitutivo do Senado     220701.0  Sim   

                            nome sigla_partido sigla_uf  id_orgao sigla_orgao  \
17                    Eli Borges            PL       TO       180        PLEN   
18                     Zé Trovão            PL       SC       180        PLEN   
19                  Gerlen Diniz            PP       AC       180        PLEN   
20                 Heitor Schuch           PSB       RS       180        PLEN   
21                 Orlando Silva         PCdoB       SP       180        PLEN   
...                          ...           ...      ...       ...         ...   
5957569        Gilvan da Federal            PL       ES       180        PLEN   
5957570      Felipe Francischini         UNIÃO       PR       180        PLEN   
5957571       Sargento Gonçalves            PL       RN       180        PLEN   
5957572   Carlos Henrique Gaguim         UNIÃO       TO       180        PLEN   
5957573  Delegado Matheus Laiola         UNIÃO       PR       180        PLEN   

         aprovacao nome_orgao  year  
17             1.0   Plenário  2023  
18             1.0   Plenário  2023  
19             1.0   Plenário  2023  
20             1.0   Plenário  2023  
21             1.0   Plenário  2023  
...            ...        ...   ...  
5957569        1.0   Plenário  2023  
5957570        1.0   Plenário  2023  
5957571        1.0   Plenário  2023  
5957572        1.0   Plenário  2023  
5957573        1.0   Plenário  2023  

[5742877 rows x 17 columns]

In [102]:
votacao_plenario['tema'].unique()

array(['Agricultura, Pecuária, Pesca e Extrativismo',
       'Estrutura Fundiária',
       'Meio Ambiente e Desenvolvimento Sustentável', 'Economia',
       'Finanças Públicas e Orçamento', nan, 'Administração Pública',
       'Cidades e Desenvolvimento Urbano',
       'Viação, Transporte e Mobilidade', 'Trabalho e Emprego',
       'Indústria, Comércio e Serviços'], dtype=object)

In [103]:
votacao_plenario['tipo'].unique()

array(['Projeto de Lei de Conversão', 'Emenda/Substitutivo do Senado',
       'Requerimento', nan,
       'Requerimento de Urgência (Art. 154, II, do RICD)',
       'Requerimento de Urgência (Art. 155 do RICD)',
       'Requerimento de Redistribuição', 'Requerimento de Apensação',
       'Requerimento de Transformação de Sessão Plenária em Comissão Geral',
       'Requerimento de Inclusão ou Retirada de Assinatura em Proposição de Iniciativa Coletiva Obrigatória',
       'Requerimento de Quebra de Interstício para Inclusão de Matéria na Ordem do Dia',
       'Requerimento de Desapensação',
       'Requerimento de Inclusão ou Retirada de Assinatura em Proposição de Iniciativa Individual',
       'Destaque para Votação em Separado', 'Destaque de Emenda',
       'Emenda Aglutinativa de Plenário',
       'Emenda de Plenário a Projeto com Urgência',
       'Emenda de Redação em Plenário', 'Redação Final',
       'Requerimento de Adiamento da Votação',
       'Requerimento de Votação pelo Pr

In [104]:
votacao_plenario['nome_orgao'].unique()

array(['Plenário'], dtype=object)

## Formas de Criar conexão entre os deputados

1. Por simularidade de votos
2. Por similaridade ponderada pelo tipo
3. Por simularidade ponderada pela relevância
4. Por similaridade ponderada por partido
5. Por vetorização

### 1. Por simularidade de votos

In [105]:
def calculate_connections_similarity(votacao):
    """
    Calculates the connections between deputies based on common votes.

    Args:
    votacao (DataFrame): DataFrame with votes that want to build the connections.

    Returns:
    dict: Dictionary of normalized connections between deputies.
    """
    # Initialize an empty dictionary to store connections
    connections = {}

    # Iterate over each proposition
    for proposition_id, votes in votacao.groupby('id_votacao'):
        # Get the list of deputies who voted on this proposition
        deputies = votes['id_deputado'].unique()
        
        # Create connections between each pair of deputies who voted the same on this proposition
        for i, deputy_a in enumerate(deputies):
            for deputy_b in deputies[i+1:]:
                if (deputy_a, deputy_b) not in connections:
                    connections[(deputy_a, deputy_b)] = 0
                connections[(deputy_a, deputy_b)] += 1

    print("Established connections between deputies")
    print(f"Sample connections: {list(connections.items())[:5]}")

    # Get the maximum weight
    max_weight = max(connections.values())
    print(f"Maximum weight: {max_weight}")

    # Normalize the weights
    for key in connections:
        connections[key] /= max_weight

    print("Normalized the weights")
    print(f"Sample normalized connections: {list(connections.items())[:5]}")

    return connections

## Formas de podar as arestas

1. Poda através de threshold

### 1. Poda através de threshold

In [106]:
def filter_connections(connections, threshold):
    """
    Filtra as conexões mais fracas com base em um threshold definido pelo usuário.

    Args:
    connections (dict): Dicionário de conexões entre deputados com pesos normalizados.
    threshold (float): Valor do threshold para filtrar as conexões.

    Returns:
    dict: Novo dicionário de conexões filtradas.
    """
    # Filtrar conexões com peso maior ou igual ao threshold
    filtered_connections = {key: value for key, value in connections.items() if value >= threshold}
    
    print(f"Filtered connections with threshold {threshold}")
    return filtered_connections

## Detecção de Comunidades

1. Leiden algorithm
2. Louvain

### 1. Leiden algorithm

In [107]:
def detect_communities_leiden(connections):
    """
    Detecta comunidades em um grafo usando o algoritmo de Leiden.

    Args:
    connections (dict): Dicionário de conexões entre deputados com pesos normalizados.

    Returns:
    tuple: Grafo do NetworkX com comunidades detectadas, layout do grafo.
    """
    # Create a graph
    G = nx.Graph()

    # Add edges to the graph with normalized weights
    for (deputy_a, deputy_b), weight in connections.items():
        G.add_edge(deputy_a, deputy_b, weight=weight)

    print("Created graph with connections")

    # Convert NetworkX graph to igraph
    nx_g = nx.Graph(G)
    ig_g = ig.Graph.TupleList(nx_g.edges(), directed=False)

    # Detect communities using Leiden algorithm
    partition = la.find_partition(ig_g, la.ModularityVertexPartition)

    # Add community information to the nodes
    community_dict = {node: community for community, nodes in enumerate(partition) for node in nodes}
    
    # Convert igraph node indices to original node labels
    mapping = {i: v for i, v in enumerate(nx_g.nodes())}
    community_dict = {mapping[node]: community for node, community in community_dict.items()}

    nx.set_node_attributes(G, community_dict, 'community')

    # Generate position using spring layout
    pos = nx.spring_layout(G, seed=42)

    return G, pos, community_dict, partition

## Plotagem dos Grafos

1. Grafos dos nós e arestas
2. Grafos pós detecção de comunidades

### 1. Grafos dos nós e arestas

In [108]:
def create_and_plot_graph(connections, title):
    """
    Cria e plota um grafo com base nas conexões fornecidas.

    Args:
    connections (dict): Dicionário de conexões entre deputados com pesos normalizados.
    title (str): Título do gráfico.

    Returns:
    None
    """
    # Create a graph
    G = nx.Graph()

    # Add edges to the graph with normalized weights
    for (deputy_a, deputy_b), weight in connections.items():
        G.add_edge(deputy_a, deputy_b, weight=weight)

    print("Created graph with connections")

    # Generate position using spring layout
    pos = nx.spring_layout(G, seed=42)

    # Extract the edges and nodes from the graph
    edge_x = []
    edge_y = []
    for edge in G.edges():
        x0, y0 = pos[edge[0]]
        x1, y1 = pos[edge[1]]
        edge_x.extend([x0, x1, None])
        edge_y.extend([y0, y1, None])

    edge_trace = go.Scatter(
        x=edge_x, y=edge_y,
        line=dict(width=0.5, color='#888'),
        hoverinfo='none',
        mode='lines')

    node_x = []
    node_y = []
    for node in G.nodes():
        x, y = pos[node]
        node_x.append(x)
        node_y.append(y)

    node_trace = go.Scatter(
        x=node_x, y=node_y,
        mode='markers+text',
        text=[str(node) for node in G.nodes()],
        textposition="bottom center",
        marker=dict(
            showscale=True,
            colorscale='YlGnBu',
            size=10,
            color=[],
            colorbar=dict(
                thickness=15,
                title='Node Connections',
                xanchor='left',
                titleside='right'
            )
        )
    )

    # Color the nodes based on the number of connections
    node_adjacencies = []
    for node, adjacencies in enumerate(G.adjacency()):
        node_adjacencies.append(len(adjacencies[1]))

    node_trace.marker.color = node_adjacencies

    # Create the figure
    fig = go.Figure(data=[edge_trace, node_trace],
                 layout=go.Layout(
                    title=title,
                    titlefont_size=16,
                    showlegend=False,
                    hovermode='closest',
                    margin=dict(b=20,l=5,r=5,t=40),
                    xaxis=dict(showgrid=False, zeroline=False),
                    yaxis=dict(showgrid=False, zeroline=False))
                    )

    fig.show()

In [109]:
connections = calculate_connections_similarity(votacao_plenario)

threshold = 0.7  
filtered_connections = filter_connections(connections, threshold)

create_and_plot_graph(filtered_connections, "Connections Between Deputies Based on Common Votes (2023)")

Established connections between deputies
Sample connections: [((204374.0, 220683.0), 152), ((204374.0, 220686.0), 126), ((204374.0, 204364.0), 114), ((204374.0, 74554.0), 112), ((204374.0, 204524.0), 97)]
Maximum weight: 164
Normalized the weights
Sample normalized connections: [((204374.0, 220683.0), 0.926829268292683), ((204374.0, 220686.0), 0.7682926829268293), ((204374.0, 204364.0), 0.6951219512195121), ((204374.0, 74554.0), 0.6829268292682927), ((204374.0, 204524.0), 0.5914634146341463)]
Filtered connections with threshold 0.7
Created graph with connections


### 2. Grafos pós detecção de comunidades

In [110]:
def plot_graph_with_communities(G, pos, title):
    """
    Plota um grafo com comunidades detectadas.

    Args:
    G (networkx.Graph): Grafo do NetworkX com comunidades detectadas.
    pos (dict): Layout do grafo.
    title (str): Título do gráfico.

    Returns:
    None
    """
    # Extract the edges and nodes from the graph
    edge_x = []
    edge_y = []
    for edge in G.edges():
        x0, y0 = pos[edge[0]]
        x1, y1 = pos[edge[1]]
        edge_x.extend([x0, x1, None])
        edge_y.extend([y0, y1, None])

    edge_trace = go.Scatter(
        x=edge_x, y=edge_y,
        line=dict(width=0.5, color='#888'),
        hoverinfo='none',
        mode='lines')

    node_x = []
    node_y = []
    node_color = []
    for node in G.nodes():
        x, y = pos[node]
        node_x.append(x)
        node_y.append(y)
        node_color.append(G.nodes[node]['community'])

    node_trace = go.Scatter(
        x=node_x, y=node_y,
        mode='markers+text',
        text=[str(node) for node in G.nodes()],
        textposition="bottom center",
        marker=dict(
            showscale=True,
            colorscale='YlGnBu',
            size=10,
            color=node_color,
            colorbar=dict(
                thickness=15,
                title='Community',
                xanchor='left',
                titleside='right'
            )
        )
    )

    # Create the figure
    fig = go.Figure(data=[edge_trace, node_trace],
                 layout=go.Layout(
                    title=title,
                    titlefont_size=16,
                    showlegend=False,
                    hovermode='closest',
                    margin=dict(b=20,l=5,r=5,t=40),
                    xaxis=dict(showgrid=False, zeroline=False),
                    yaxis=dict(showgrid=False, zeroline=False))
                    )

    fig.show()

In [111]:
connections = calculate_connections_similarity(votacao_plenario)

threshold = 0.7  
filtered_connections = filter_connections(connections, threshold)

G, pos, community_dict, partition = detect_communities_leiden(filtered_connections)

plot_graph_with_communities(G, pos, "Communities Detected with Leiden Algorithm (2023)")

Established connections between deputies
Sample connections: [((204374.0, 220683.0), 152), ((204374.0, 220686.0), 126), ((204374.0, 204364.0), 114), ((204374.0, 74554.0), 112), ((204374.0, 204524.0), 97)]
Maximum weight: 164
Normalized the weights
Sample normalized connections: [((204374.0, 220683.0), 0.926829268292683), ((204374.0, 220686.0), 0.7682926829268293), ((204374.0, 204364.0), 0.6951219512195121), ((204374.0, 74554.0), 0.6829268292682927), ((204374.0, 204524.0), 0.5914634146341463)]
Filtered connections with threshold 0.7
Created graph with connections


## Avaliar Comunidade

1. Modularidade: Mede a densidade de conexões dentro das comunidades em comparação com as conexões entre comunidades.
2. NMI (Normalized Mutual Information): Mede a similaridade entre duas partições, útil para comparar resultados de diferentes algoritmos.
3. ARI (Adjusted Rand Index): Avalia a similaridade entre duas partições considerando o acaso.

In [112]:
def evaluate_communities(G, community_dict, partition):
    """
    Avalia a qualidade das comunidades detectadas usando diferentes métricas.

    Args:
    G (networkx.Graph): Grafo do NetworkX.
    community_dict (dict): Dicionário com as comunidades detectadas.
    partition (list): Partição das comunidades.

    Returns:
    dict: Dicionário com as métricas de avaliação.
    """
    # Calcular modularidade
    modularity = partition.modularity

    # Preparar dados para NMI e ARI
    labels_true = [community_dict[node] for node in G.nodes()]
    labels_pred = [partition.membership[list(G.nodes()).index(node)] for node in G.nodes()]

    # Calcular NMI
    nmi = normalized_mutual_info_score(labels_true, labels_pred)

    # Calcular ARI
    ari = adjusted_rand_score(labels_true, labels_pred)

    return {'modularity': modularity, 'nmi': nmi, 'ari': ari}

In [113]:
metrics = evaluate_communities(G, community_dict, partition)

print("Metrics for Leiden:", metrics)

Metrics for Leiden: {'modularity': 0.06220752806002151, 'nmi': 1.0, 'ari': 1.0}
